In [1]:
import sys
import xlsxwriter
import pandas as pd
import sys
import psycopg2
import os
from dotenv import load_dotenv
from datetime import date

today = date.today()
load_dotenv()

#configurar la conexion a la base de datos
DB_USERNAME = os.getenv('DB_USERNAME')
DB_DATABASE = os.getenv('DB_DATABASE')
DB_PASSWORD = os.getenv('DB_PASSWORD')
DB_PORT = os.getenv('DB_PORT')
DB_HOST=os.getenv('DB_HOST')

cnx = psycopg2.connect(
        user=DB_USERNAME,
        password=DB_PASSWORD,
        host=DB_HOST,
        port=DB_PORT,
        database=DB_DATABASE
    )

cursor=cnx.cursor()

In [2]:
#read graduated database MASTER
data=pd.read_excel(r'V:\Archivos Seguimiento de Egresados\2025\Proyecto de Seguimiento de Egresados Posgrado_2025\GraduadosMaeTotal.xlsx')

In [3]:
#read graduated database DOCTORATE
data_doc=pd.read_excel(r'V:\Archivos Seguimiento de Egresados\2025\Proyecto de Seguimiento de Egresados Posgrado_2025\GraduadosDocTotal.xlsx')

In [4]:
eg_posgrado=pd.read_sql('select * from egresados_posgrado',cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [5]:
original_data=pd.concat([data,data_doc],ignore_index=True)

In [6]:
original_data.columns

Index(['Número de Cuenta', 'Nombre', 'Primer Apellido', 'Segundo Apellido',
       'Sexo', 'Fecha de Nacimiento', 'Nacionalidad', 'Teléfono Principal',
       'Teléfono Emergencia', 'Teléfono Otro', 'Correo electrónico',
       'Programa de Posgrado', 'Nivel', 'Plan de estudios',
       'Semestre de ingreso', 'Semestre de egreso',
       'Fecha de obtención del grado', 'Teléfonos'],
      dtype='object')

In [7]:
corrupted_data=pd.read_sql("select * from egresados_posgrado where fuente='internet' and sexo is not null and fec_nac is not null",cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [8]:
original_data['Número de Cuenta']=original_data['Número de Cuenta'].astype(str)

In [2]:
b20=pd.read_sql("select * from respuestas20 where completed='1' and gen_dgae='2020'",cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [3]:
for col in ['fec_capt','updated_at','created_at']:
    b20[col]=b20[col].astype(str).apply(lambda x: x[:10])

In [4]:
b20.to_excel('base2020_4_noviembre_2025_fecha recortada.xlsx')

In [70]:
bdep_malu=pd.read_excel(r'V:\Malu, David & Felipe\base20 Depuración completa.xlsx')

In [71]:
len(bdep_malu)

6649

In [72]:
len(b20)

5023

In [73]:
bdep_malu=bdep_malu.rename(columns={'ncr2':'ncr2_depurada','ncr7_a':'ncr7_a_depurada','ncr12_a':'ncr12_a_depurada','ncr3':'ncr3_depurada','ncr4':'ncr4_depurada'})

In [77]:
bunida=b20.merge(bdep_malu[['registro','ncr2_depurada','ncr7_a_depurada','ncr12_a_depurada','ncr3_depurada','ncr4_depurada']],on='registro',how='left')

In [85]:
bunida[['ncr3_depurada','ncr3']]

ncr3_depurada  ncr3
0               2.0   2.0
1               2.0   2.0
2               2.0   2.0
3               2.0   2.0
4               NaN   NaN
...             ...   ...
5018            NaN   NaN
5019            1.0   1.0
5020            2.0   2.0
5021            NaN   NaN
5022            2.0   2.0

[5023 rows x 2 columns]

In [84]:
bunida.loc[(bunida['ncr3_depurada'].isnull()),'ncr3_depurada']=bunida['ncr3']

In [86]:
bunida.to_excel('base2020_4_noviembre_2025_depurada.xlsx')

In [9]:
# unemployeed but seeking
len(b20.loc[b20['ncr1'].isin([4,7,8])])

613

In [93]:
b20['ncr21'].astype(float).max()

700000.0

In [94]:
10*.16

1.6

In [23]:
# Further study
# len(b20.loc[b20['ncr24'].isin([1])])
len(b20.loc[(b20['ncr1'].isin([2,6]))&(b20['ncr24'].isin([1]))])+len(b20.loc[(b20['ncr1'].isin([7,5]))])

149

In [37]:
map_ocupaciones={
33 : 33,
34 : 34,
35 : 35,
36 : 36,
37 : 37,
38 : 38,
40 : 40,
45 : 21,
46 : 16,
47 : 24,
48 : 25,
49 : 32,
50 : 27,
51 : 28,
52 : 46,
53 : 30,
54 : 17,
56 : 18,
57 : 19,
58 : 45,
59 : 44,
60 : 60,
61 :61 ,
0:0,
}

In [47]:
b20['nar16'].value_counts()

46    1128
48     824
37     394
52     384
47     306
53     298
51     286
34     227
45     206
35     179
49     176
38     109
61      91
57      91
54      88
50      55
56      54
59      47
36      43
58      22
33       9
60       4
40       2
Name: nar16, dtype: int64

In [115]:
egresados_data=pd.read_sql("select * from egresados where anio_egreso=2020 and fuente='dgae'",cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [102]:
#Limpiar promedio
egresados_data.loc[egresados_data['promedio']>100,'promedio']=egresados_data.loc[egresados_data['promedio']>100,'promedio']/100

In [118]:
egresados_data['generacion']=egresados_data['generacion'].fillna(2016)

In [126]:
b_unida=bunida.merge(egresados_data[['cuenta','generacion','promedio','extras','fec_nac','sexo','sistema']],how='inner',on='cuenta')

In [138]:
b_unida.loc[b_unida['registro']!=1430].to_excel('base2020_5_noviembre_datos_dgae.xlsx')

In [137]:
len(b_unida.loc[b_unida['registro']!=1430])

5009

In [50]:
for col in ['nar14','nar15','nar16']:
    # b20[col]=b20[col].map(map_ocupaciones)
    print(b20[col].value_counts())

0.0     3307
16.0     369
25.0      64
24.0      57
33.0      52
21.0      44
38.0      27
19.0      24
30.0      19
46.0      19
36.0      16
32.0      14
17.0      14
61.0      13
18.0      11
28.0      10
34.0      10
45.0       8
37.0       6
44.0       6
35.0       4
27.0       2
60.0       1
Name: nar14, dtype: int64
33    1959
16     693
25     586
24     450
19     261
30     221
34     131
36     110
21      81
32      80
38      66
17      64
35      63
18      63
61      37
28      31
44      31
46      29
45      28
37      21
40       8
27       8
60       2
Name: nar15, dtype: int64
16    1128
25     824
37     394
46     384
24     306
30     298
28     286
34     227
21     206
35     179
32     176
38     109
61      91
19      91
17      88
27      55
18      54
44      47
36      43
45      22
33       9
60       4
40       2
Name: nar16, dtype: int64


In [51]:
b20.to_excel('base2020_4_noviembre_ocupaciones_recodificadas.xlsx')

In [ ]:
# inhabiles
# len(b20.loc[b20['ncr24'].isin([1])])
len(b20.loc[(b20['ncr1'].isin([3,6]))])+len(b20.loc[b20['ncr1'].isin([5])])

In [111]:
b20.loc[b20['registro']==332,'ncr1']

1786    1.0
Name: ncr1, dtype: float64

In [9]:
#emprendimiento
corrupted_data

Empty DataFrame
Columns: [id, cuenta, nombre, paterno, materno, anio_egreso, plan, grado, sexo, status, created_at, updated_at, fec_nac, fec_grad, nacionalidad, programa, fuente]
Index: []

In [26]:
for i in range(len(corrupted_data)):
    original_row=original_data.loc[original_data['Número de Cuenta']==corrupted_data.iloc[i]['cuenta']]
    print(f"update egresados_posgrado set plan='{original_row['Plan de estudios'].values[0]}',programa='{original_row['Programa de Posgrado'].values[0]}',anio_egreso='{original_row['Semestre de egreso'].values[0][:4]}' where id={corrupted_data.iloc[i]['id']};")
    # print(corrupted_data['cuenta'].values[i],original_row['Número de Cuenta'].values[0],corrupted_data['id'].values[i])
      

update egresados_posgrado set plan='MAESTRÍA EN ADMINISTRACIÓN',programa='PROGRAMA DE POSGRADO EN CIENCIAS DE LA ADMINISTRACIÓN',anio_egreso='2021' where id=3368;
update egresados_posgrado set plan='MAESTRÍA EN ALTA DIRECCIÓN',programa='PROGRAMA DE POSGRADO EN CIENCIAS DE LA ADMINISTRACIÓN',anio_egreso='2020' where id=3711;
update egresados_posgrado set plan='MAESTRÍA EN HISTORIA',programa='PROGRAMA DE POSGRADO EN HISTORIA',anio_egreso='2021' where id=8075;
update egresados_posgrado set plan='MAESTRÍA EN ADMINISTRACIÓN',programa='PROGRAMA DE POSGRADO EN CIENCIAS DE LA ADMINISTRACIÓN',anio_egreso='2022' where id=4253;
update egresados_posgrado set plan='MAESTRÍA EN ALTA DIRECCIÓN',programa='PROGRAMA DE POSGRADO EN CIENCIAS DE LA ADMINISTRACIÓN',anio_egreso='2019' where id=4075;
update egresados_posgrado set plan='MAESTRÍA EN AUDITORÍA',programa='PROGRAMA DE POSGRADO EN CIENCIAS DE LA ADMINISTRACIÓN',anio_egreso='2019' where id=1648;
update egresados_posgrado set plan='MAESTRÍA EN ADMINI

In [27]:
for i in range(len(corrupted_data)):
    original_row=original_data.loc[original_data['Número de Cuenta']==corrupted_data.iloc[i]['cuenta']]
    print(f"update egresados_posgrado set fuente='base original' where id={corrupted_data.iloc[i]['id']};")
   

update egresados_posgrado set fuente='base original' where id=3368;
update egresados_posgrado set fuente='base original' where id=3711;
update egresados_posgrado set fuente='base original' where id=8075;
update egresados_posgrado set fuente='base original' where id=4253;
update egresados_posgrado set fuente='base original' where id=4075;
update egresados_posgrado set fuente='base original' where id=1648;
update egresados_posgrado set fuente='base original' where id=3448;
update egresados_posgrado set fuente='base original' where id=2452;
update egresados_posgrado set fuente='base original' where id=2229;
update egresados_posgrado set fuente='base original' where id=18589;
update egresados_posgrado set fuente='base original' where id=5864;
update egresados_posgrado set fuente='base original' where id=2604;
update egresados_posgrado set fuente='base original' where id=9946;
update egresados_posgrado set fuente='base original' where id=2499;
update egresados_posgrado set fuente='base orig

In [60]:
data.columns

Index(['Número de Cuenta', 'Nombre', 'Primer Apellido', 'Segundo Apellido',
       'Sexo', 'Fecha de Nacimiento', 'Nacionalidad', 'Teléfono Principal',
       'Teléfono Emergencia', 'Teléfono Otro', 'Correo electrónico',
       'Programa de Posgrado', 'Nivel', 'Plan de estudios',
       'Semestre de ingreso', 'Semestre de egreso',
       'Fecha de obtención del grado', 'Teléfonos'],
      dtype='object')

In [23]:
len(data)

15217

In [62]:
# Migrar egresados de posgrado maestria/doctorado
start=0
end=len(data)
query='INSERT INTO egresados_posgrado(cuenta,nombre,paterno,' \
'                                     materno,anio_egreso,fec_nac,' \
'                                     sexo,fec_grad,plan,' \
'                                     programa,nacionalidad) values(%s,%s,%s, %s,%s,%s, %s,%s,%s, %s,%s)'

for i in range(start,end):
    print(i)
    cursor.execute(query,tuple([
        str(data['Número de Cuenta'].values[i]),
        str(data['Nombre'].values[i]),
        str(data['Primer Apellido'].values[i]),

        str(data['Segundo Apellido'].values[i]),
        data['Semestre de egreso'].values[i][:4],
        str(data['Fecha de Nacimiento'].values[i]),

        str(data['Sexo'].values[i]),
        data['Fecha de obtención del grado'].values[i],
        str(data['Plan de estudios'].values[i]),

        str(data['Programa de Posgrado'].values[i]),
        str(data['Nacionalidad'].values[i]),

                                   ]))

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [42]:
data.columns

Index(['Número de Cuenta', 'Nombre', 'Primer Apellido', 'Segundo Apellido',
       'Sexo', 'Fecha de Nacimiento', 'Nacionalidad', 'Teléfono Principal',
       'Teléfono Emergencia', 'Teléfono Otro', 'Correo electrónico',
       'Programa de Posgrado', 'Nivel', 'Plan de estudios',
       'Semestre de ingreso', 'Semestre de egreso',
       'Fecha de obtención del grado', 'Teléfonos'],
      dtype='object')

In [ ]:
cnx.commit()

In [ ]:
data['Teléfono Otro']=data['Teléfono Otro'].fillna(0).astype(str)

In [72]:
data['Teléfono Emergencia']=data['Teléfono Emergencia'].fillna(0).astype(str)

In [68]:
data['Teléfono Principal']=data['Teléfono Principal'].fillna(0).astype(str)

In [ ]:
#migrar losd atos de contacto
#SUBIR DATOS DE CONTACTO
# for i in range(len(data)):
#set interval:
strt=0
end=len(data)
for i in range(strt,end):
    cuenta=str(int(data['Número de Cuenta'].values[i]))
    Eg=pd.read_sql("select * from egresados_posgrado where cuenta='"+cuenta+"'",cnx)
    tels_exits=pd.read_sql("select * from telefonos where cuenta = '"+cuenta+"'",cnx)
    mails_exits=pd.read_sql("select * from correos where cuenta = '"+cuenta+"'",cnx)
    print(i,cuenta,Eg['nombre'].values[0],len(Eg))
    # print(len(tels_exits),'telefonos')
    #incrustar a la base SQL los telefonos de la base en excel
    #Teléfono Principal
    if(len(data['Teléfono Principal'].values[i])>8):
        if(data['Teléfono Principal'].values[i][:3]=='044'):
            tel=data['Teléfono Principal'].values[i][3:]
        else:
            tel=data['Teléfono Principal'].values[i]
        if(tel not in tels_exits['telefono'].values):
            query=("insert into telefonos(cuenta, telefono,status,descripcion) values('%s','%s','%s','%s')"%tuple([cuenta,tel,0,'casa']))
            cursor.execute(query)
            print(tel,'insertado ::::TEL INSERTED::::')
    #Teléfono Emergencia
    if(len(str(data['Teléfono Emergencia'].values[i]))>8):
        # print(data['Teléfono Emergencia'].values[i])
        if(data['Teléfono Emergencia'].values[i][:3]=='044'):
            tel=data['Teléfono Emergencia'].values[i][3:]
        else:
            tel=data['Teléfono Emergencia'].values[i]
        if(tel not in tels_exits['telefono'].values):
            query=("insert into telefonos(cuenta, telefono,status,descripcion) values('%s','%s','%s','%s')"%tuple([cuenta,tel,0,'celular']))
            cursor.execute(query)
      #Teléfono otro
    if(len(str(data['Teléfono Otro'].values[i]))>8):
        # print(data['Teléfono Otro'].values[i])
        if(data['Teléfono Otro'].values[i][:3]=='044'):
            tel=data['Teléfono Otro'].values[i][3:]
        else:
            tel=data['Teléfono Otro'].values[i]
        if(tel not in tels_exits['telefono'].values):
            query=("insert into telefonos(cuenta, telefono,status,descripcion) values('%s','%s','%s','%s')"%tuple([cuenta,tel,0,'celular']))
            cursor.execute(query)
    #correo
    if((len(str(data['Correo electrónico'].values[i]))>6)&('@' in str(data['Correo electrónico'].values[i]) )):
        if(data['Correo electrónico'].values[i][:1]=='-'):
            correo=data['Correo electrónico'].values[i][1:]
        else:
            correo=data['Correo electrónico'].values[i]
        if(correo not in mails_exits['correo'].values):
            query=("insert into correos(cuenta, correo,status) values('%s','%s','%s')"%tuple([cuenta,correo,0]))
            cursor.execute(query)
            print(correo,'insertado ::::MAIL INSERTED::::')
cnx.commit()

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

0 81800603 MIGUEL ANGEL 1
5557822689.0 insertado ::::TEL INSERTED::::
migueloncito@yahoo.com insertado ::::MAIL INSERTED::::
1 404009595 VICTOR HUGO 1
5559087389.0 insertado ::::TEL INSERTED::::
vhvico@hotmail.com insertado ::::MAIL INSERTED::::
2 500008575 MARIA ANGELICA 1
5559424655.0 insertado ::::TEL INSERTED::::
ma_gelic@hotmail.com insertado ::::MAIL INSERTED::::
3 505010247 FELICITAS ALEJANDRA 1
3123125124.0 insertado ::::TEL INSERTED::::
alejandra_valladares@hotmail.com insertado ::::MAIL INSERTED::::
4 511015670 MAYRA VERONICA 1
6566178286.0 insertado ::::TEL INSERTED::::
mayigil@yahoo.com.mx insertado ::::MAIL INSERTED::::
5 511023143 JUANA 1
6696699800041.0 insertado ::::TEL INSERTED::::
juany_gc@hotmail.com insertado ::::MAIL INSERTED::::
6 512010173 LUIS RAUL 1
6566188819.0 insertado ::::TEL INSERTED::::
luimarti@uacj.mx insertado ::::MAIL INSERTED::::
7 512029423 LUIS ENRIQUE 1
56831325.0 insertado ::::TEL INSERTED::::
luisenrique.espinosa@gmail.com insertado ::::MAIL INS

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

9 512029801 LARA ABRIL 1
6566481411.0 insertado ::::TEL INSERTED::::
spyder4712@gmail.com insertado ::::MAIL INSERTED::::
10 512029825 NESTOR DANIEL 1
65616561089144.0 insertado ::::TEL INSERTED::::
d07drakar26@gmail.com insertado ::::MAIL INSERTED::::
11 512453435 CECIL EDUARDO 1
59322338271.0 insertado ::::TEL INSERTED::::
cecileduaguirre@gmail.com insertado ::::MAIL INSERTED::::
12 512453583 DIEGO MARCELO 1
72859335.0 insertado ::::TEL INSERTED::::
dcordero@ucacue.edu.ec insertado ::::MAIL INSERTED::::
13 512453662 KATINA VANESSA 1
59372818337.0 insertado ::::TEL INSERTED::::
bermeovanessa@yahoo.com insertado ::::MAIL INSERTED::::
14 513006601 MA. DEL ROCIO 1
2414176257.0 insertado ::::TEL INSERTED::::
rociocastilloe@yahoo.com.mx insertado ::::MAIL INSERTED::::
15 513021736 SYLVIA 1
525543299910.0 insertado ::::TEL INSERTED::::
smeljem@itam.mx insertado ::::MAIL INSERTED::::
16 506016840 THEODORE 1
3336416908.0 insertado ::::TEL INSERTED::::
radioquest@yahoo.com insertado ::::MAIL I

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

...

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

4394 512452531 JOSE ROBERTO 1
5545069143.0 insertado ::::TEL INSERTED::::
bbetoo@gmail.com insertado ::::MAIL INSERTED::::
4395 514014964 CRISTIAN MANUEL 1
6646238934.0 insertado ::::TEL INSERTED::::
cristian.manuel@gmail.com insertado ::::MAIL INSERTED::::
4396 514351643 MARIA JOSE 1
5552435258.0 insertado ::::TEL INSERTED::::
mariajosealviarc@gmail.com insertado ::::MAIL INSERTED::::
4397 516492858 ZOILA ELENA 1
5154255284.0 insertado ::::TEL INSERTED::::
zoelvesa@hotmail.com insertado ::::MAIL INSERTED::::
4398 507011862 JUAN CARLOS 1
5556590439.0 insertado ::::TEL INSERTED::::
jclagunam@yahoo.com insertado ::::MAIL INSERTED::::
4399 402078696 MARIO ERNESTO 1
5555279228.0 insertado ::::TEL INSERTED::::
marioer_hur@hotmail.com insertado ::::MAIL INSERTED::::
4400 88320124 ARMANDO 1
armgomriv@yahoo.es insertado ::::MAIL INSERTED::::
4401 97143372 CHRISTIAN EUGENIO 1
55103546.0 insertado ::::TEL INSERTED::::
christian.lopeznegrete@gmail.com insertado ::::MAIL INSERTED::::
4402 95512237

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

4411 304028890 CRISTINA 1
55675273.0 insertado ::::TEL INSERTED::::
cristina.goqui@gmail.com insertado ::::MAIL INSERTED::::
4412 509009823 LUIS DANIEL 1
6672576567.0 insertado ::::TEL INSERTED::::
luisdellamary@gmail.com insertado ::::MAIL INSERTED::::
4413 509011325 JOSE MARTIN 1
5558701752.0 insertado ::::TEL INSERTED::::
montevivo100@gmail.com insertado ::::MAIL INSERTED::::
4414 515048593 MAYRENE OBDULIA 1
5567304773.0 insertado ::::TEL INSERTED::::
mguimarais@yahoo.es insertado ::::MAIL INSERTED::::


c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site

In [54]:
cnx.commit()

In [78]:
cnx.close()

In [ ]:
#read titulados database
data=pd.read_excel(r'V:\Archivos Seguimiento de Egresados\2023\PadronTitulacionPVEU_DGOAE2021-2022-2023A.xlsx')

In [5]:
data=data.rename(columns={'Número de cuenta':'cuenta'})

In [6]:
data.columns

Index(['Num', 'Ejercicio', 'Nivel', 'Convocatoria', 'Estatus', 'cuenta',
       'Promedio', 'Primer apellido', 'Segundo apellido', 'Nombre(s)', 'Edad',
       'Teléfono', 'Teléfono Celular', 'CURP', 'Correo', 'ClavePlantel',
       'Plantel', 'ClaveCarrera', 'Carrera', 'Sistema', 'Sexo',
       'FechaNacimiento', 'LugarNacimiento2', 'LugarNacimiento', 'FAC_FACULT',
       'CAR_CARRER', 'CAR_CARRER0'],
      dtype='object')

In [7]:
data['cuenta']

0       313149564
1       418123966
2       315013809
3       315110616
4       314297589
          ...    
8182    312263579
8183    417140487
8184    316210214
8185    315125243
8186    313288717
Name: cuenta, Length: 8187, dtype: int64

In [9]:
egresados20=pd.read_sql('select * from egresados where muestra=3',cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [13]:
len(egresados20)

19544

In [11]:
egresados20['cuenta']=egresados20['cuenta'].astype(int)

In [44]:
new_data['Teléfono']

0      5.554859e+09
1      5.525421e+09
2      5.583675e+09
3      5.558980e+09
4      5.529157e+09
           ...     
870    5.521571e+09
871    5.516593e+09
872    5.555617e+09
873    5.555828e+09
874    5.558586e+09
Name: Teléfono, Length: 875, dtype: float64

In [14]:
new_data=egresados20.merge(data[['cuenta','Teléfono', 'Teléfono Celular','Correo']],on='cuenta',how='inner')

In [53]:
# for i in range(len(new_data)):
for i in range(len(new_data)):
    actualized=0
    cuenta=str(new_data['cuenta'].values[i])
    #traer todos los telefonos y correos del egresado
    telefonos=pd.read_sql(f"select * from telefonos where cuenta = '{cuenta}'",cnx)
    telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
    correos=pd.read_sql(f"select * from correos where cuenta = '{cuenta}'",cnx)
    #verificar que no exista ya
    tel1=str(int(new_data['Teléfono'].values[i]))
    if(tel1 not in telefonos['telefono'].values):
            actualized=1
            query=("insert into telefonos(cuenta, telefono,status,descripcion) values('%s','%s','%s','%s')"%tuple([cuenta,tel1,0,'casa']))
            cursor.execute(query)
            print(tel,'insertado ::::TEL INSERTED::::')
    
    tel1=str(int(new_data['Teléfono Celular'].values[i]))
    if(tel1 not in telefonos['telefono'].values):
            actualized=1
            query=("insert into telefonos(cuenta, telefono,status,descripcion) values('%s','%s','%s','%s')"%tuple([cuenta,tel1,0,'celular']))
            cursor.execute(query)
            print(tel,'insertado ::::TEL INSERTED::::')
    correo=new_data['Correo'].values[i]
    if(correo not in correos['correo'].values):
            query=("insert into correos(cuenta, correo,status) values('%s','%s','%s')"%tuple([cuenta,correo,0]))
            cursor.execute(query)
            print(tel,'insertado ::::TEL INSERTED::::')
    query="update egresados set actualized='2025-06-19' where muestra=3 and cuenta='"+cuenta+"';"
    if(actualized==1):
        print(cuenta,query)
    cursor.execute(query)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

52571343 insertado ::::TEL INSERTED::::
314003339 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='314003339';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
414007598 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='414007598';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
312037990 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='312037990';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313159251 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313159251';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313201697 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313201697';


c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313285620 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313285620';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
414007495 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='414007495';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313136113 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313136113';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
311004753 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='311004753';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
311089484 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='311089484';


c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

...

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
417019642 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='417019642';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
314171247 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='314171247';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
314004903 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='314004903';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
314013710 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='314013710';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313091834 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313091834';


c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
416094837 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='416094837';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313199679 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313199679';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313307861 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313307861';
52571343 insertado ::::TEL INSERTED::::
52571343 insertado ::::TEL INSERTED::::
313309054 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='313309054';
52571343 insertado ::::TEL INSERTED::::
311026612 update egresados set actualized='2025-06-19' where muestra=3 and cuenta='311026612';


c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\734902692.py:7: FutureWarning: The default value of regex will change from True to False in a future version.
  telefonos['telefono']=telefonos['telefono'].str.replace('.0','')
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy conn

In [51]:
cnx.close()

In [35]:
tels=pd.read_sql('select * from telefonos limit 200',cnx)
print(tels['cuenta'].unique())

['84265696' '107000781' '310048815' '311153150' '402098238' '312156367'
 '313018152' '313106176' '313122514' '313133624' '313338094' '313027969'
 '313159251' '313201697' '313260715' '313285620' '313316836' '313002315'
 '313048003' '313079724' '313095715' '312049959' '313130654' '313152465'
 '313224137' '313294736' '313337437' '312298339' '313059106' '313087314'
 '313088359' '313092563' '313106389' '313129238' '313137581' '313163317'
 '313175455' '313193134' '313193268' '313225347' '313236543' '313266597'
 '313280429' '313319260' '313320019' '313347382' '313047910' '313052396'
 '313107984' '313178308' '313251795' '110004338' '313208500' '313236172'
 '313296060' '313325519' '313035023' '110000488' '313005309' '313025886'
 '313053991' '313147261' '313201312' '313088586' '313233841' '313239197'
 '313285118' '313337217' '313357471' '304199132' '84077390' '311222560'
 '312218548' '312288147' '415031440' '313150502' '313195066' '313290752'
 '313352579' '313081673' '313091872' '313129276' '313

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


C:\Users\fgonzalez\AppData\Local\Temp\ipykernel_19116\3330742538.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  tels['telefono'].str.replace('.0','')


0         7634589
1      5563191554
2      5535716627
3        55661563
4      5553374364
          ...    
195      55413644
196      55592663
197        555936
198    5543727374
199      55559771
Name: telefono, Length: 200, dtype: object

In [34]:
correos=pd.read_sql("""select egresados_posgrado.*,correos.correo from correos inner join 
                    egresados_posgrado on correos.cuenta=egresados_posgrado.cuenta
                     where egresados_posgrado.status is  null or egresados_posgrado.status=10
""",cnx)

c:\Users\fgonzalez\AppData\Local\Programs\Python\Python310\lib\site-packages\pandas\io\sql.py:762: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


In [37]:
correos['nombre_completo']=correos['nombre']+' '+correos['paterno']+' '+correos['materno']

In [41]:
correos=correos.drop_duplicates(subset=['correo'],keep='first')

In [45]:
correos[['nombre_completo','cuenta','plan','programa','correo']].to_excel('Correos_no_contestadas_posgrado.xlsx')

In [ ]:
correos['programa']

0        PROGRAMA DE POSGRADO EN CIENCIAS POLÍTICAS Y S...
1        PROGRAMA DE POSGRADO EN CIENCIAS POLÍTICAS Y S...
2        PROGRAMA DE POSGRADO EN CIENCIAS POLÍTICAS Y S...
3        PROGRAMA DE POSGRADO EN CIENCIAS POLÍTICAS Y S...
4        PROGRAMA DE MAESTRÍA Y DOCTORADO EN CIENCIAS M...
                               ...                        
19270    PROGRAMA DE MAESTRÍA EN DOCENCIA PARA LA EDUCA...
19271    PROGRAMA DE MAESTRÍA Y DOCTORADO EN CIENCIAS Q...
19272                   PROGRAMA DE POSGRADO EN INGENIERÍA
19273                                                 None
19274    PROGRAMA DE MAESTRÍA Y DOCTORADO EN CIENCIAS Q...
Name: programa, Length: 18983, dtype: object

: 

In [46]:
correos['cuenta'].value_counts()

308007473    4
309008590    3
412012442    3
313172540    3
308184057    3
            ..
93278986     1
96397338     1
93399151     1
307155966    1
80418120     1
Name: cuenta, Length: 18274, dtype: int64